In [1]:
import itertools
import pandas as pd
import numpy as np
import toytree
import toyplot
import arviz as az
import pymc3 as pm

### Load tree

In [3]:
EXCLUDE = [
    'Quercus|Quercus|Leucomexicana|Q.species', 
    'Quercus|Quercus|Roburoids|Q.vulcanica',
    'Quercus|Quercus|Roburoids|Q.imeretina', 
    'Quercus|Lobatae|Erythromexicana|Q.lowilliamsii', 
    'Quercus|Lobatae|Agrifoliae|Q.oxyadenia',
    'Quercus|Quercus|Dumosae|Q.pacifica',
    'Quercus|Quercus|Roburoids|Q.kotschyana',
    'Quercus|Quercus|Roburoids|Q.cedrorum', 
    'Quercus|Lobatae|Agrifoliae|Q.tamalpaiensis',
    'Cerris|Cyclobalanopsis|Semiserrata|Q.litoralis', 
    'Cerris|Cyclobalanopsis|Semiserrata|Q.patelliformis',
    'Cerris|Cyclobalanopsis|Glauca|Q.multinervis', 
    'Cerris|Ilex|Himalayansubalpine|Q.sp.nov.',
]

TREE = toytree.tree("/home/henry/oaks-thesis/full_crown2.tre").drop_tips(EXCLUDE)

# find duplicates (label ends in 1 or 2, we'll drop the 2)
DUPS = [i for i in TREE.get_tip_labels() if i.endswith('2')]
TREE = TREE.drop_tips(DUPS)

# relabel kept duplicate tips by stripping 1 from end
TREE = TREE.set_node_values(
    feature="name", 
    values={nidx: TREE.idx_dict[nidx].name.strip("1") for nidx in TREE.idx_dict}
)

# Scale tree to 1.0 length
TREE = TREE.mod.node_scale_root_height(1.0)

In [8]:
# Get crown nodes for eight clades.
clades = [
    "Quercus|Quercus", # teal
    "Quercus|Virentes", # orange
    "Quercus|Ponticae", # blue
    "Quercus|Protobalanus", # pink
    "Quercus|Lobatae", # green
    "Cerris|Ilex", # yellow
    "Cerris|Cerris", # tan
    "Cerris|Cyclobalanopsis", # gray
]
crowns = {
    TREE.get_mrca_idx_from_tip_labels(wildcard=i): i for i in clades
}
crowns

{419: 'Quercus|Quercus',
 420: 'Quercus|Virentes',
 434: 'Quercus|Ponticae',
 447: 'Quercus|Protobalanus',
 455: 'Quercus|Lobatae',
 450: 'Cerris|Ilex',
 451: 'Cerris|Cerris',
 457: 'Cerris|Cyclobalanopsis'}

In [52]:
# draw the tree
TREE.draw(
    layout='d', 
    edge_colors=TREE.get_edge_values_mapped({
            j: toytree.colors[i] for i,j in enumerate(crowns)
        }),
    tip_labels=False,
    height=350,
    node_labels=[
        str(i) if int(i) in crowns else "" 
        for i in TREE.get_node_values("idx", 1, 1)
    ],
    node_labels_style={
        "font-size": "16px",
        "-toyplot-anchor-shift": "15px",
    },
);

<svg class="toyplot-canvas-Canvas" height="350.0px" id="tb421381eb5e64f9cb41ee0e8fd448f58" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 1000.0 350.0" width="1000.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> 419 420 434 447 450 451 455 457

In [10]:
# make group index (gidx)
crown_dict = {i: TREE.get_tip_labels(i) for i in crowns}
gidx = np.zeros(TREE.ntips, dtype=int)
for tidx, tip in enumerate(TREE.get_tip_labels()):
    for cidx, clade in enumerate(crown_dict):
        if tip in crown_dict[clade]:
            gidx[tidx] = cidx
gidx

array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1,
       1, 1, 1, 2, 2, 3, 3, 3, 3, 3, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
       4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
       4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
       4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 5, 5, 5, 5, 5, 5, 5, 5,
       5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 6, 6, 6, 6, 6, 6, 6, 6, 6, 6, 6, 6,
       6, 6, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7,
       7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7])

In [131]:
# True param values
𝛼_mean = 0.05
𝛼_std = 0.02
𝛽_mean = 3.0
𝛽_std = 0.2
𝜓_mean = 0.0
𝜓_std = 0.33

# 8 different clade effects on rate of RI (used for partial-pooling data)
𝜓_Quercus_mean = -0.8
𝜓_Quercus_std = 0.2
𝜓_Virentes_mean = -3.5
𝜓_Virentes_std = 0.05
𝜓_Ponticae_mean = -5.0
𝜓_Ponticae_std = 0.05
𝜓_Protobalanus_mean = 5.0
𝜓_Protobalanus_std = 0.1
𝜓_Lobatae_mean = 0.5
𝜓_Lobatae_std = 0.2
𝜓_Ilex_mean = 1.0
𝜓_Ilex_std = 0.15
𝜓_Cerris_mean = 5.0
𝜓_Cerris_std = 0.15
𝜓_Cyclobalanopsis_mean = 3.5
𝜓_Cyclobalanopsis_std = 0.15

In [132]:
SPECIES_DATA = pd.DataFrame({
    "Species": ["Quercus " + "{}".format(
        TREE.idx_dict[idx].name.split("|")[-1].split(".")[-1]) for idx in range(len(TREE.get_tip_labels()))],
    "b": np.random.normal(𝛽_mean, 𝛽_std, TREE.ntips),
    "psi": np.random.normal(𝜓_mean, 𝜓_std, TREE.ntips),
    "psi_x": np.concatenate([
        np.random.normal(𝜓_Quercus_mean, 𝜓_Quercus_std, len(gidx[gidx == 0])),
        np.random.normal(𝜓_Virentes_mean, 𝜓_Virentes_std, len(gidx[gidx == 1])),
        np.random.normal(𝜓_Ponticae_mean, 𝜓_Ponticae_std, len(gidx[gidx == 2])),
        np.random.normal(𝜓_Protobalanus_mean, 𝜓_Protobalanus_std, len(gidx[gidx == 3])),
        np.random.normal(𝜓_Lobatae_mean, 𝜓_Lobatae_std, len(gidx[gidx == 4])),
        np.random.normal(𝜓_Ilex_mean, 𝜓_Ilex_std, len(gidx[gidx == 5])),
        np.random.normal(𝜓_Cerris_mean, 𝜓_Cerris_std, len(gidx[gidx == 6])),
        np.random.normal(𝜓_Cyclobalanopsis_mean, 𝜓_Cyclobalanopsis_std, len(gidx[gidx == 7])),
    ]),
    "gidx": gidx
})

In [133]:
SPECIES_DATA

Species         b       psi     psi_x  gidx
0       Quercus arizonica  2.649839  0.124749 -0.829386     0
1    Quercus oblongifolia  3.375341  0.027754 -0.856423     0
2           Quercus laeta  2.967354 -0.262966 -0.469912     0
3        Quercus ajoensis  2.909137  0.177614 -0.864610     0
4      Quercus turbinella  2.728273 -0.439628 -0.549844     0
..                    ...       ...       ...       ...   ...
226           Quercus rex  3.265054 -0.123982  3.702592     7
227       Quercus chungii  3.254171  0.036968  3.299497     7
228      Quercus delavayi  3.210858 -0.440764  3.485134     7
229    Quercus championii  3.269819 -0.300722  3.704606     7
230         Quercus gilva  2.612676  0.085809  3.249456     7

[231 rows x 5 columns]

### Generate crossing data

In [134]:
def get_dist(tree, idx0, idx1):
    "returns the genetic distance between two nodes on a tree"
    dist = tree.treenode.get_distance(
        tree.idx_dict[idx0], 
        tree.idx_dict[idx1],
    )
    return dist

# get all combinations of two sampled taxa
a, b = zip(*itertools.combinations(range(TREE.ntips), 2))

# organize into DF and get genetic distance between pairs
DATA = pd.DataFrame({
    "sidx0": a,
    "sidx1": b,
    "dist": [get_dist(TREE, i, j) / 2 for (i, j) in zip(a, b)],
})

# get pairwise velocity
DATA['b'] = (
    np.random.normal(𝛽_mean, 𝛽_std, DATA.shape[0])
)

DATA['velo'] = (
    DATA['b']
    + SPECIES_DATA['psi'][DATA.sidx0].values
    + SPECIES_DATA['psi'][DATA.sidx1].values
)

DATA['velo_x'] = (
    DATA['b']
    + SPECIES_DATA['psi_x'][DATA.sidx0].values
    + SPECIES_DATA['psi_x'][DATA.sidx1].values
)

DATA['intercept'] = np.random.normal(𝛼_mean, 𝛼_std, DATA.shape[0])

# get logits
DATA['logit_b'] = (
    1 / (1 + np.exp(-(DATA.intercept + DATA.dist * DATA.b)))
)
DATA['logit'] = (
    1 / (1 + np.exp(-(DATA.intercept + DATA.dist * DATA.velo)))
)
DATA['logit_x'] = (
    1 / (1 + np.exp(-(DATA.intercept + DATA.dist * DATA.velo_x)))
)

# get RI estimates
DATA['RI_pooled'] = np.random.binomial(n=1, p=DATA.logit_b / DATA.logit_b.max())
DATA['RI_unpooled'] = np.random.binomial(n=1, p=DATA.logit / DATA.logit.max())
DATA['RI_partpooled'] = np.random.binomial(n=1, p=DATA.logit_x / DATA.logit_x.max())

DATA.head()

sidx0  sidx1      dist         b      velo    velo_x  intercept   logit_b  \
0      0      1  0.001046  2.746947  2.899450  1.061138   0.027633  0.507626   
1      0      2  0.002093  2.901469  2.763252  1.602171   0.011850  0.504480   
2      0      3  0.004185  3.270655  3.573019  1.576659   0.075311  0.522235   
3      0      4  0.008371  2.981583  2.666704  1.602353   0.073360  0.524560   
4      0      5  0.016741  3.137269  3.501146  1.595426   0.002633  0.513785   

      logit   logit_x  RI_pooled  RI_unpooled  RI_partpooled  
0  0.507666  0.507185          1            0              0  
1  0.504408  0.503801          0            1              1  
2  0.522551  0.520466          0            0              0  
3  0.523902  0.521680          0            1              0  
4  0.515307  0.507335          0            0              1

In [135]:
NSAMPLES = 1000
SAMPLE = DATA.sample(NSAMPLES).copy().reset_index(drop=True)
SAMPLE.head()

sidx0  sidx1      dist         b      velo    velo_x  intercept   logit_b  \
0     19    205  1.000000  2.862798  2.842064  5.557401   0.035540  0.947764   
1     32    168  1.000000  2.841939  2.503688  3.171095   0.056308  0.947760   
2    216    224  0.862857  3.225487  1.869283  9.851656   0.027151  0.943229   
3     66    137  0.927411  2.797488  1.427397  2.107891   0.074170  0.935148   
4     58    172  1.000000  3.025176  3.817973  3.234370   0.083669  0.957256   

      logit   logit_x  RI_pooled  RI_unpooled  RI_partpooled  
0  0.946728  0.996290          1            1              1  
1  0.928242  0.961853          1            1              1  
2  0.837545  0.999802          1            1              1  
3  0.801859  0.883814          1            1              1  
4  0.980192  0.965043          1            1              1

### Visualize data

In [19]:
def logit_plot(dist, logit, RI):
    canvas = toyplot.Canvas(width=500, height=250)
    ax0 = canvas.cartesian(
        label="pooled data (function)",
        xlabel="Genetic dist.",
        ylabel="Logit function",
        grid=(1, 2, 0),
    )
    ax1 = canvas.cartesian(
        label="pooled data (observation)",
        xlabel="Genetic dist.",
        ylabel="RI",
        grid=(1, 2, 1),
    )

    # points are jittered on x-axis for visibility
    ax0.scatterplot(
        dist,
        logit,
        size=5,
        opacity=0.33,
        color=toyplot.color.Palette()[0],
    );
    ax1.scatterplot(
        dist,
        RI,
        size=10,
        opacity=0.2,
        marker="|",
        mstyle={
            "stroke": toyplot.color.Palette()[1],
            "stroke-width": 3,
        },
    );
    return canvas, (ax0, ax1)

In [136]:
logit_plot(SAMPLE.dist, SAMPLE.logit_b, SAMPLE.RI_pooled);

<svg class="toyplot-canvas-Canvas" height="250.0px" id="t73ae1685ab744b0fa576b930f0a4e8f0" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 500.0 250.0" width="500.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> <g class="toyplot-Datum" style="fill:rgb(40%,76.1%,64.7%);fill-opacity:1.0;opacity:0.33;stroke:rgb(40%,76.1%,64.7%);stroke-opacity:1.0" transform="translate(170.6594842313108, 77

In [137]:
logit_plot(SAMPLE.dist, SAMPLE.logit, SAMPLE.RI_unpooled);

<svg class="toyplot-canvas-Canvas" height="250.0px" id="td86ca7a941f04955a7f1470fb8215239" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 500.0 250.0" width="500.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> <g class="toyplot-Datum" style="fill:rgb(40%,76.1%,64.7%);fill-opacity:1.0;opacity:0.33;stroke:rgb(40%,76.1%,64.7%);stroke-opacity:1.0" transform="translate(170.6594842313108, 62

In [138]:
logit_plot(SAMPLE.dist, SAMPLE.logit_x, SAMPLE.RI_partpooled);

<svg class="toyplot-canvas-Canvas" height="250.0px" id="tc2a9bd7c0f6b4052821a0cc17491e816" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 500.0 250.0" width="500.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> <g class="toyplot-Datum" style="fill:rgb(40%,76.1%,64.7%);fill-opacity:1.0;opacity:0.33;stroke:

### Define models

In [23]:
def toytrace(trace, var_names, titles):
    """
    Plot posterior trace with toyplot
    """
    nvars = len(var_names)
    
    # setup canvase
    canvas = toyplot.Canvas(width=500, height=200 * nvars)
    
    # store axes
    axes = []
    
    # iter over params
    for pidx, param in enumerate(var_names):
        
        # get param posterior
        posterior = trace.get_values(param)
        
        # setup axes 
        ax = canvas.cartesian(grid=(nvars, 1, pidx))
        ax.y.show = False
        ax.x.spine.style = {"stroke-width": 1.5}
        ax.x.ticks.labels.style = {"font-size": "12px"}
        ax.x.ticks.show = True
        ax.x.label.text = f"param='{titles[pidx]}'"        
        
        # iterate over shape of param
        for idx in range(posterior.shape[1]):
            mags, bins = np.histogram(posterior[:, idx], bins=100)
            ax.plot(bins[1:], mags, stroke_width=2, opacity=0.6)
        axes.append(ax)
    return canvas, axes

In [35]:
def pooled_logistic(x, y, **kwargs):
    
    # define model
    with pm.Model() as model:  

        # parameters and error
        𝛼 = pm.Normal('𝛼', mu=0., sigma=10., shape=1)
        𝛽 = pm.Normal('𝛽', mu=0., sigma=10., shape=1)
        
        # link function
        effect = 𝛼 + 𝛽 * x
        logit = pm.Deterministic("logit", pm.invlogit(effect))
        
        # data likelihood
        y = pm.Bernoulli("y", p=logit, observed=y)
        
        # sample posterior, skip burnin
        trace = pm.sample(**kwargs)[1000:]
    
        # show summary table
        stats = pm.summary(trace)
        
    # organize results
    result_dict = {
        'model': model, 
        'trace': trace,
        'stats': stats,
    }
    return result_dict

In [36]:
def unpooled_logistic(x, y, idx0, idx1, **kwargs):
    
    # define model
    with pm.Model() as model:
        
        # indexers
        sidx0 = pm.Data("spp_idx0", idx0.values)
        sidx1 = pm.Data("spp_idx1", idx1.values)

        # parameters and error
        𝜓_mean = pm.Normal('𝜓_mean', mu=0., sigma=5., shape=1)
        𝜓_std = pm.HalfNormal('𝜓_std', 5., shape=1)
        𝜓_offset = pm.Normal('𝜓_offset', mu=0, sigma=1., shape=TREE.ntips)
        𝜓 = pm.Deterministic('𝜓', 𝜓_mean + 𝜓_std * 𝜓_offset)
        𝛼 = pm.Normal('𝛼', mu=0., sigma=10., shape=1)
        𝛽 = pm.Normal('𝛽', mu=0., sigma=10., shape=1)
        
        # link function
        effect = 𝛼 + (𝛽 + 𝜓[sidx0] + 𝜓[sidx1]) * x
        logit = pm.Deterministic("logit", pm.invlogit(effect))
        
        # data likelihood
        y = pm.Bernoulli("y", p=logit, observed=y)
        
        # sample posterior, skip burnin
        trace = pm.sample(**kwargs)[1000:]
    
        # show summary table
        stats = pm.summary(trace)
        
    # organize results
    result_dict = {
        'model': model, 
        'trace': trace,
        'stats': stats,
    }
    return result_dict

In [37]:
def partpooled_logistic(x, y, idx0, idx1, gidx, **kwargs):
    
    # define model
    with pm.Model() as model:
        
        # indexers
        sidx0 = pm.Data("spp_idx0", idx0)
        sidx1 = pm.Data("spp_idx1", idx1)
        gidx = pm.Data("gidx", gidx)

        # parameters and error
        𝜓_mean = pm.Normal('𝜓_mean', mu=0., sigma=5., shape=8)
        𝜓_std = pm.HalfNormal('𝜓_std', 5., shape=8)
        𝜓_offset = pm.Normal('𝜓_offset', mu=0, sigma=1., shape=TREE.ntips)
        𝜓 = pm.Deterministic('𝜓', 𝜓_mean[gidx] + 𝜓_std[gidx] * 𝜓_offset)
        𝛽 = pm.Normal('𝛽', mu=0., sigma=10., shape=1)
        𝛼 = pm.Normal('𝛼', mu=0., sigma=10., shape=1)
        
        # linear model prediction
        effect = 𝛼 + (𝛽 + 𝜓[sidx0] + 𝜓[sidx1]) * x
        logit = pm.Deterministic("logit", pm.invlogit(effect))
        
        # data likelihood (normal distributed errors)
        y = pm.Bernoulli("y", p=logit, observed=y)

        # sample posterior, skip burnin
        trace = pm.sample(**kwargs)[1000:]

        # show summary table
        stats = pm.summary(trace)
        
    # organize results
    result_dict = {
        'model': model, 
        'trace': trace,
        'stats': stats,
    }
    return result_dict

In [98]:
# MCMC sampler kwargs
sample_kwargs = dict(
    tune=10000,
    draws=10000,
    target_accept=0.99,
    return_inferencedata=False,
    progressbar=True,
)

In [142]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_pooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# pooled model
pooled_sub = pooled_logistic(*model_args[:2], **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using jitter+adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛽, 𝛼]


Sampling 4 chains for 10_000 tune and 10_000 draw iterations (40_000 + 40_000 draws total) took 222 seconds.
The number of effective samples is smaller than 25% for some parameters.


In [143]:
pooled_sub['stats']

mean     sd  hdi_3%  hdi_97%  mcse_mean  mcse_sd  ess_mean  \
𝛼[0]       -0.083  0.258  -0.561    0.407      0.003    0.002    7791.0   
𝛽[0]        3.709  0.377   2.987    4.402      0.004    0.003    7813.0   
logit[0]    0.974  0.005   0.964    0.983      0.000    0.000   15364.0   
logit[1]    0.974  0.005   0.964    0.983      0.000    0.000   15364.0   
logit[2]    0.957  0.007   0.944    0.970      0.000    0.000   20274.0   
...           ...    ...     ...      ...        ...      ...       ...   
logit[995]  0.974  0.005   0.964    0.983      0.000    0.000   15364.0   
logit[996]  0.966  0.006   0.954    0.977      0.000    0.000   17572.0   
logit[997]  0.966  0.006   0.955    0.977      0.000    0.000   17428.0   
logit[998]  0.952  0.007   0.938    0.965      0.000    0.000   21878.0   
logit[999]  0.966  0.006   0.954    0.977      0.000    0.000   17572.0   

             ess_sd  ess_bulk  ess_tail  r_hat  
𝛼[0]         7447.0    7779.0    9700.0    1.0  
𝛽[0]         7802.0    7789.0    9707.0    1.0  
logit[0]    15361.0   15184.0   17144.0    1.0  
logit[1]    15361.0   15184.0   17144.0    1.0  
logit[2]    20267.0   20055.0   18433.0    1.0  
...             ...       ...       ...    ...  
logit[995]  15361.0   15184.0   17144.0    1.0  
logit[996]  17566.0   17350.0   17887.0    1.0  
logit[997]  17422.0   17207.0   17949.0    1.0  
logit[998]  21869.0   21630.0   18755.0    1.0  
logit[999]  17566.0   17350.0   17887.0    1.0  

[1002 rows x 11 columns]

In [144]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_unpooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# unpooled model
unpooled_sub = unpooled_logistic(*model_args[:4], **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using jitter+adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛽, 𝛼, 𝜓_offset, 𝜓_std, 𝜓_mean]


Sampling 4 chains for 10_000 tune and 10_000 draw iterations (40_000 + 40_000 draws total) took 8543 seconds.
The number of effective samples is smaller than 25% for some parameters.


In [145]:
toytrace(unpooled_sub['trace'], ['𝜓_mean', '𝜓_offset', '𝜓'], ['psi-mean', 'psi-offset', 'psi-spp']);

<svg class="toyplot-canvas-Canvas" height="600.0px" id="t29e008cbe88a48ebb9375c9f3c487ca5" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 500.0 600.0" width="500.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> <path d="M 50.0 149.92348890589136 L 53.83759511599193 150.0 L 57.67519023198386 150.0 L 61.51278534797578 150.0 L 65.35038046396771 149.77046671767405 L 69.18797557995964 149.77046671767405 L 73.02557069595156 149.3114001530222 L 76.8631658119435 149.38791124713083 L 80.70076092793543 149.08186687069625 L 84.53835604392737 149.0053557765876 L 88.37595115991927 148.46977811782708 L 92.21354627591123 148.39326702371844 L 96.05114139190313 147.628156082632 L 99.88873650789506 147.39862280030604 L 103.72633162388699 146.4804896710023 L 107.56392673987892 146.40397857689365 L 111.40152185587087 144.10864575363428 L 115.23911697186279 144.9502677888294 L 119.0767120878547 142.42540168324408 L 122.91430720384663 139.36495791889823 L 126.75190231983858 139.67100229533284 L 130.58949743583048 136.3045141545524 L 134.42709255182243 135.00382555470543 L 138.26468766781434 130.1071155317521 L 142.1022827838063 127.2762050497322 L 145.9398778997982 124.44529456771231 L 149.77747301579015 118.4009181331293 L 153.61506813178204 115.5700076511094 L 157.45266324777398 113.88676358071922 L 161.29025836376593 110.29074215761284 L 165.12785347975785 102.79265493496555 L 168.96544859574976 97.58990053557767 L 172.8030437117417 92.76970160673298 L 176.64063882773362 86.18974751338943 L 180.47823394372557 83.35883703136955 L 184.31582905971752 76.39632746748279 L 188.1534241757094 73.33588370313696 L 191.99101929170135 69.12777352716144 L 195.82861440769327 62.16526396327468 L 199.6662095236852 61.706197398622805 L 203.50380463967716 55.5087987758225 L 207.34139975566907 56.04437643458301 L 211.17899487166102 58.798775822494264 L 215.01658998765294 54.43764345830146 L 218.85418510364485 50.8416220351951 L 222.6917802196368 58.33970925784239 L 226.52937533562869 50.0 L 230.3669704516206 50.076511094108646 L 234.20456556761258 62.54781943381791 L 238.0421606836045 62.853863810252484 L 241.8797557995964 64.84315225707726 L 245.71735091558833 68.66870696250956 L 249.55494603158024 73.02983932670237 L 253.39254114757225 83.35883703136955 L 257.23013626356413 89.86228003060444 L 261.06773137955605 90.78041315990819 L 264.90532649554797 97.13083397092578 L 268.7429216115399 102.41009946442233 L 272.58051672753186 109.90818668706964 L 276.4181118435238 111.66794185156849 L 280.2557069595157 116.33511859219588 L 284.0933020755076 121.15531752104054 L 287.9308971914996 125.66947207345066 L 291.7684923074915 127.04667176740627 L 295.6060874234834 129.4185156847743 L 299.44368253947533 135.30986993114 L 303.2812776554672 138.21729150726856 L 307.1188727714592 138.67635807192042 L 310.95646788745114 142.5019127773527 L 314.79406300344306 142.9609793420046 L 318.631658119435 143.34353481254783 L 322.46925323542695 145.25631216526395 L 326.30684835141886 145.6388676358072 L 330.1444434674108 147.01606732976282 L 333.9820385834027 147.1690895179801 L 337.8196336993946 148.0107115531752 L 341.6572288153866 147.8576893649579 L 345.4948239313785 148.77582249426166 L 349.3324190473704 149.0053557765876 L 353.17001416336234 149.3114001530222 L 357.00760927935426 149.3114001530222 L 360.84520439534623 149.77046671767405 L 364.68279951133815 149.61744452945678 L 368.52039462733006 149.8469778117827 L 372.357989743322 149.54093343534814 L 376.195584859314 149.92348890589136 L 380.03317997530587 150.0 L 383.8707750912978 150.0 L 387.7083702072897 149.8469778117827 L 391.5459653232816 149.8469778117827 L 395.3835604392736 150.0 L 399.221

In [146]:
# show plot of TRUE vs. ESTIMATED rates
c, a, m = toyplot.scatterplot(
    unpooled_sub['trace']['𝜓'].mean(axis=0),         # estimated
    SPECIES_DATA['psi'],                             # true
    width=400,
    height=250,
    xlabel="ESTIMATED species velocity",
    ylabel="TRUE species velocity",
    # color=[toyplot.color.Palette()[i] for i in SPECIES_DATA.gidx],
);

<svg class="toyplot-canvas-Canvas" height="250.0px" id="t05dae3f797e04867808078ca5c334165" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 400.0 250.0" width="400.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> 0.6 0.7 0.8 0.9 ESTIMATED species velocity -1 0 1 TRUE species velocity

In [139]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_partpooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# partpooled model
partpooled_sub = partpooled_logistic(*model_args, **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using jitter+adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛼, 𝛽, 𝜓_offset, 𝜓_std, 𝜓_mean]


Sampling 4 chains for 10_000 tune and 10_000 draw iterations (40_000 + 40_000 draws total) took 5161 seconds.
The number of effective samples is smaller than 25% for some parameters.


In [140]:
toytrace(partpooled_sub['trace'], ['𝜓_mean', '𝜓_offset', '𝜓'], ['psi-mean', 'psi-offset', 'psi-spp']);

<svg class="toyplot-canvas-Canvas" height="600.0px" id="ta725012e4e04465aa4e5c1ab6b9f434d" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 500.0 600.0" width="500.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> <path d="M 156.31192088139875 149.80759980759981 L 157.74938899480514 149.90379990379992 L 159.18685710821148 149.80759980759981 L 160.62432522161782 149.90379990379992 L 162.06179333502422 149.75949975949976 L 163.49926144843053 149.71139971139968 L 164.9367295618369 149.71139971139968 L 166.37419767524327 149.56709956709958 L 167.8116657886496 149.18229918229918 L 169.24913390205597 149.37469937469936 L 170.68660201546234 149.13419913419912 L 172.1240701288687 148.60509860509862 L 173.56153824227505 148.4126984126984 L 174.99900635568142 148.12409812409814 L 176.43647446908778 147.30639730639732 L 177.87394258249412 146.44059644059644 L 179.31141069590046 146.007696007696 L 180.74887880930683 145.5747955747956 L 182.1863469227132 144.99759499759497 L 183.62381503611954 143.26599326599327 L 185.0612831495259 142.1115921115921 L 186.49875126293225 140.13949013949014 L 187.9362193763386 139.5141895141895 L 189.37368748974498 137.97498797498795 L 190.81115560315135 136.67628667628668 L 192.2486237165577 132.6839826839827 L 193.68609182996403 130.61568061568062 L 195.12355994337042 127.87397787397786 L 196.56102805677676 126.47907647907648 L 197.9984961701831 123.92977392977394 L 199.4359642835895 119.4083694083694 L 200.87343239699584 117.96536796536796 L 202.31090051040218 115.51226551226551 L 203.74836862380857 109.2111592111592 L 205.1858367372149 107.86435786435787 L 206.62330485062125 101.32275132275133 L 208.06077296402762 101.13035113035114 L 209.498241077434 97.04184704184705 L 210.93570919084033 96.8013468013468 L 212.37317730424672 94.78114478114477 L 213.81064541765306 90.35594035594036 L 215.2481135310594 93.72294372294373 L 216.6855816444657 89.05723905723906 L 218.1230497578721 92.37614237614238 L 219.56051787127848 90.88504088504088 L 220.99798598468485 89.53823953823954 L 222.4354540980912 91.5103415103415 L 223.87292221149755 96.07984607984608 L 225.31039032490392 93.43434343434343 L 226.7478584383103 100.07215007215007 L 228.18532655171663 99.35064935064936 L 229.622794665123 100.93795093795093 L 231.06026277852934 105.45935545935545 L 232.4977308919357 108.29725829725828 L 233.93519900534207 110.990860990861 L 235.37266711874838 113.87686387686387 L 236.81013523215478 115.41606541606542 L 238.24760334556112 118.73496873496875 L 239.68507145896746 122.87157287157285 L 241.12253957237382 126.09427609427608 L 242.56000768578022 128.45117845117844 L 243.9974757991866 131.86628186628187 L 245.43494391259296 134.12698412698413 L 246.8724120259993 135.56998556998556 L 248.3098801394056 137.63828763828764 L 249.74734825281195 138.985088985089 L 251.18481636621834 142.01539201539202 L 252.62228447962468 141.5824915824916 L 254.05975259303108 144.22799422799423 L 255.49722070643742 144.51659451659452 L 256.9346888198438 144.03559403559404 L 258.37215693325015 146.68109668109668 L 259.8096250466565 147.6911976911977 L 261.24709316006283 147.6911976911977 L 262.6845612734692 147.7873977873978 L 264.12202938687557 148.02789802789803 L 265.5594975002819 148.60509860509862 L 266.9969656136883 148.94179894179894 L 268.4344337270946 149.37469937469936 L 269.871901840501 149.47089947089944 L 271.3093699539074 149.66329966329968 L 272.7468380673137 149.80759980759981 L 274.18430618072006 149.80759980759981 L 275.62177429412645 149.71139971139968 L 277.0592424075328 149.80759980759981 L 278.49671052093913 149.90379990379992 L 279.93417863434547 149.90379990379992 L 281.3716467477518 149.903799

In [141]:
# show plot of TRUE vs. ESTIMATED rates
c, a, m = toyplot.scatterplot(
    partpooled_sub['trace']['𝜓'].mean(axis=0),         # estimated
    SPECIES_DATA['psi_x'],                             # true
    width=400,
    height=250,
    xlabel="ESTIMATED species velocity",
    ylabel="TRUE species velocity",
    color=[toytree.colors[i] for i in SPECIES_DATA.gidx],
);

<svg class="toyplot-canvas-Canvas" height="250.0px" id="tcf561f7bd00a4e6ab2084d2d4ca781fc" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 400.0 250.0" width="400.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> -8 -4 0 4 8 ESTIMATED species velocity -5 0 5 TRUE species velocity